In [1]:
from __future__ import print_function
from gensim.models import KeyedVectors

# Creating the model
model = KeyedVectors.load_word2vec_format('./statics/model.vec')


In [2]:
word = model.wv.most_similar(positive=['男人','丈夫'], negative=['女人'])

print(word)

[('妻子', 0.7083192467689514), ('前夫', 0.621699333190918), ('婚后他', 0.61387038230896), ('结婚', 0.6128422021865845), ('前妻', 0.5968211889266968), ('未婚夫', 0.59489905834198), ('女儿', 0.5853056311607361), ('再婚', 0.5817466974258423), ('离异', 0.5811194181442261), ('离婚', 0.5760695934295654)]


In [3]:
word = model.wv.most_similar(positive=['男人','爸爸'], negative=['女人'])

print(word)

[('妈妈', 0.6678740978240967), ('我妈妈', 0.6257693767547607), ('爷爷', 0.6198632717132568), ('随妈妈', 0.586621880531311), ('著妈妈', 0.586142897605896), ('爸爸妈妈', 0.5826867818832397), ('温妈妈', 0.5775355696678162), ('吴妈妈', 0.5761699676513672), ('由妈妈', 0.5751886367797852), ('奶奶家', 0.5732123851776123)]


主要问题：

1 水果 苹果 月季花 油彩 画布 框
这样的题目人类可以了解是静物，但是word2vic确会匹配出苹果酒等等食物，不适用于目标为配色的搜索匹配.（人类理解为静物也不符合目标为配色的搜索匹配）

2 1993年 人名 等内容 词库中没有，可以解决方案：1添加在wiki的全文之后再次训练，2直接去掉这些内容


另外发现一个新的信息源，某些图画有discribe

例如： 黄涛，1968年生于重庆。1980年毕业于中央美术学院油画系。中国美术家协会会员，贵州师范大学教授。其作品《银妆》获中国首届油画大展银奖。1992年参加中国油画展，1995年参加中国现代艺术作品展（瑞典）。作品多为海外机构及国内收藏家收藏。他的作品画面沉静而温暖，色彩明快，想像质朴，笔致透逸，洋溢着抒情而活跃的生命律动。


In [4]:
import zhconv
print(zhconv.convert(u'關藝術','zh-cn'))

关艺术


In [21]:
import csv
import numpy as np
import pandas as pd

file_name = '../data/artwork_sample.csv'
artwork_sample = pd.read_csv(file_name)
artwork_sample.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10048 entries, 0 to 10047
Data columns (total 22 columns):
id                  10048 non-null object
title               10019 non-null object
other_titles        1 non-null object
artwork_category    10001 non-null object
artwork_type        10017 non-null object
display_price       17 non-null object
calc_price          17 non-null object
year                10017 non-null object
technique           17 non-null float64
mounting            17 non-null float64
display_size        10000 non-null object
calc_size           9505 non-null float64
description         6110 non-null object
image_url           9985 non-null object
icon_img_url        1 non-null object
desc_origin         4 non-null object
desc_origin_url     9984 non-null object
info_update_time    9980 non-null object
created_at          9983 non-null object
updated_at          9983 non-null object
comments_count      9983 non-null float64
likes_count         9983 non-null flo

In [22]:
artwork_sample['title'] = artwork_sample['title'].fillna('无')
artwork_sample['description'] = artwork_sample['description'].fillna('无')
artwork_sample.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10048 entries, 0 to 10047
Data columns (total 22 columns):
id                  10048 non-null object
title               10048 non-null object
other_titles        1 non-null object
artwork_category    10001 non-null object
artwork_type        10017 non-null object
display_price       17 non-null object
calc_price          17 non-null object
year                10017 non-null object
technique           17 non-null float64
mounting            17 non-null float64
display_size        10000 non-null object
calc_size           9505 non-null float64
description         10048 non-null object
image_url           9985 non-null object
icon_img_url        1 non-null object
desc_origin         4 non-null object
desc_origin_url     9984 non-null object
info_update_time    9980 non-null object
created_at          9983 non-null object
updated_at          9983 non-null object
comments_count      9983 non-null float64
likes_count         9983 non-null fl

In [23]:
## generator and normal function

In [25]:
artwork_sample['vector'] = range(len(artwork_sample))

In [24]:
import pickle

f = open('./statics/frequency','rb')
frequency = pickle.load(f)
f.close()


In [31]:
import jieba

artwork_vector = [0]*len(artwork_sample)

for i in range(len(artwork_sample)):

    text = artwork_sample.title[i]
    #text = artwork_sample.title[i].replace(' ','')
    #text = text.replace('年作','')
    try :
        word_list = list(jieba.cut(text))
    except AttributeError:
        word_list = [text]
    word_list = [i for i in word_list if i !=' ']

    
    # try:
    #     word_list.remove('\u3000')
    # except ValueError:
    #     pass

    
    print(word_list)
    # try: 
    #     vic_list = [model.wv[k] for k in word_list] 
    # except KeyError:
    #     pass
    
    
    
    vic_list = []
    for k in word_list:
        try: 
            vic_list.append(model.wv[k])
        except KeyError: 
            pass

    if len (vic_list)> 0 :
        title_vic = sum (vic_list[j]/(frequency[word_list[j]]+5000) for j in range(len(vic_list)))/ len(vic_list)
        artwork_vector[i] = title_vic
        print(model.similar_by_vector(title_vic, topn=1))
    else:
        title_vic = vic_list
        artwork_vector[i] = title_vic
        print(word_list)
    


['1971', '年作', 'CORETAN', 'RASA', 'III', '（', 'SCRIBBLES', 'III', '）', 'Acrylic', 'on', 'canvas']
[('III', 0.8281570076942444)]
['2003', '年作', '海礁', '水彩', '纸']
[('海礁', 0.9139806628227234)]
['东北角', '渔村', '油画', '画布']
[('东北角', 0.7821638584136963)]
['绿海', '深处', '有', '人家', '水彩', '纸本']
[('绿海', 0.8544210195541382)]
['国师', '玄奘']
[('国师', 0.838575005531311)]
['2014', '年作', '我心', '光明', '布面', '油画']
[('我心', 0.8749476671218872)]
['1983', '年作', '气', '之', '150', '压克力', '纸本']
[('压克力', 0.8772505521774292)]
['1980', '年作', '游鱼', '纸本', '水彩']
[('游鱼', 0.9521528482437134)]
['1989', '年作', '风景', '油画']
[('1989', 0.8171392679214478)]
['木刻水印', '福禄', '鸳鸯', '纸本', '木刻水印']
[('木刻水印', 0.8857547044754028)]
['呼唤', '丙烯', '画布']
[('丙烯', 0.7687095403671265)]
['2003', '年作', '水', '布面', '油彩']
[('油彩', 0.8830803632736206)]
['荒漠', '独行', '版画']
[('独行', 0.7978836297988892)]
['2001', '年作', '光荣', '与', '梦想', '布面', '油画']
[('光荣', 0.9190068244934082)]
['1931', '年作', '自杀者', '黑白', '木刻']
[('自杀者', 0.8523649573326111)]
['2008', '年作', '男人', '布面',

[('美人鱼', 0.824758768081665)]
['现代', '版画', '《', '广阔天地', '》']
[('广阔天地', 0.9960891604423523)]
['1986', '年作', '白塔', '纸上', '水彩']
[('白塔', 0.8341835737228394)]
['2011', '年作', '寂寞', '的', '夏天', '水', '彩纸', '本']
[('彩纸', 0.8551714420318604)]
['坐', '着', '的', '人体', '布面', '油画']
[('人体', 0.7753586769104004)]
['2005', '年作', '女人', '水粉', '纸本']
[('水粉', 0.9535192251205444)]
['安宁', '的', '教堂', '·', '春雪', '（', '无图', '）', '布面', '油画']
[('春雪', 0.7951678037643433)]
['鸟', '布面', '油画']
[('鸟', 0.958675742149353)]
['1994', '年作', '浴女', '油彩', '纸板']
[('浴女', 0.8416507244110107)]
['2004', '年作', '悠久', '的', '文化', '开出', '灿烂', '的', '花', '布面', '丙烯']
[('灿烂', 0.6815353631973267)]
['蓝韵', '纸本', '油画']
[('纸本', 0.9999809265136719)]
['2005', '年作', '慰藉', '之浴', '布面', '油画']
[('之浴', 0.9154964089393616)]
['小山村', '布面', '油画']
[('小山村', 0.9946823120117188)]
['1996', '年作', '一个', '女人', '的', '后背', 'Ⅰ', '水印', '照片']
[('后背', 0.7273724675178528)]
['南京路', '油画']
[('南京路', 0.9998985528945923)]
['鸡冠花', '布面', '油彩']
[('鸡冠花', 0.974729061126709)]
['2003', '年作',

[('理想', 0.9043380618095398)]
['2005', '年作', '水', '里面', '布面', '油画']
[('水', 0.7170469760894775)]
['约', '1930', '年代', '作', '黄山', '风景', '（', '两幅', '）', '银盐', '相纸', '摄影', '原框', '一对']
[('相纸', 0.8487046957015991)]
['2006', '年作', '青岛', '风景', '2006', 'NO.9', '布面', '油画']
[('NO.9', 0.9322290420532227)]
['2004', '年作', '湖', '布面', '油画']
[('湖', 0.9571845531463623)]
['1991', '年作', '秋', '布面', '油画']
[('1991', 0.7954818606376648)]
['海之夜', '纸本', '版画']
[('海之夜', 0.9971293210983276)]
['1991', '年作', '美式', '快餐', '布面', '油画']
[('美式', 0.8582353591918945)]
['40', '年代', '作', '京剧', '人物', '纸本', '水粉']
[('水粉', 0.8710565567016602)]
['2001', '年作', '天使', '合唱团', '丝网', '印刷', '画布']
[('合唱团', 0.7815908193588257)]
['侍女', '图', '布面']
[('侍女', 0.9930980801582336)]
['1972', '年作', 'Canto', 'Pisan', '-', '致美琴', '（', '共', '十六', '件', '）', '铜版', '版画']
[('-', 0.6934295892715454)]
['襄阳', '公园', '纸本', '水彩', '\u2003']
[('\u2003', 0.8126328587532043)]
['绿', '社会', '布面', '油画']
[('绿', 0.9448822736740112)]
['风景', '布面', '油画']
[('风景', 0.873799085617

[('油彩', 0.8184298276901245)]
['行走', '布面', '油彩']
[('行走', 0.9031152129173279)]
['灰韵', '系列', '之一', '布面', '油画']
[('系列', 0.9921581745147705)]
['戏剧', '人物', '油画']
[('戏剧', 0.9963439106941223)]
['2014', '年作', '零度', '空间', '布面', '油画']
[('零度', 0.9913507103919983)]
['悟', '布面', '油画']
[('悟', 0.9877262115478516)]
['Parlemen', '（', 'Parliament', '）']
[('（', 0.9957315325737)]
['1990', '年作', '晨', '石版']
[('石版', 0.8254822492599487)]
['FRUIT', 'SELLER', 'OIL', 'ON', 'CANVAS']
[('ON', 0.8518772125244141)]
['Triptych', 'acrylic', 'on', 'canvas']
[('acryliconcanvas', 0.8861551284790039)]
['2002', '年作', '游戏规则', '亚麻布', '油画']
[('亚麻布', 0.7983829975128174)]
['1998', '年作', '版纳', '风情', '布面', '油画']
[('版纳', 0.9594690203666687)]
['Atomsfir', 'Bali', '(', 'Bali', 'Atmosphere', ')', 'oil', 'on', 'canvas']
[('80M2LiviaBenavides', 0.7993423938751221)]
['Borome', '岛', '的', '沐浴', '妇人', '们', '油彩', '板']
[('岛', 0.6972205638885498)]
['Balinese', 'beauty', 'holding', 'a', 'rijstbald', 'oil', 'on', 'canvas']
[('emphasizes', 0.86892

[('思索', 0.8563072681427002)]
['穿越', '腾格里', '布面', '油画']
[('腾格里', 0.9414880871772766)]
['1992', '年作', '法学', '教授', '油彩', '画布']
[('法学', 0.9115849137306213)]
['2005', '年作', '花卉', '布面', '油彩']
[('油彩', 0.9398257732391357)]
['2007', '年作', '镜子', '布面', '油画']
[('镜子', 0.9682090878486633)]
['RED', 'BULL', 'OIL', 'ON', 'CANVAS']
[('COMMUNICATION', 0.8310450315475464)]
['The', 'light', 'from', 'left', 'acrylic', 'on', 'canvas']
[('thereafter', 0.8741751909255981)]
['油画', '周庄', '油画', '框']
[('周庄', 0.859892725944519)]
['2003', '年作', '卡拉', 'OK', '综合', '材料', '帆布']
[('OK', 0.8283082246780396)]
['1999', '年作', '舞者', '布面', '油画']
[('舞者', 0.9735716581344604)]
['1950', '年作', '毛泽东', '会晤', '斯大林', '布面', '油画']
[('斯大林', 0.8172109127044678)]
['少女', '油彩', '画布']
[('油彩', 0.8666057586669922)]
['1992', '年作', '莫拿哥', '海岸', '油画', '画布']
[('海岸', 0.8036770820617676)]
['Communication', 'Series', '（', 'set', 'of', 'six', 'works', '）', 'chromogenic', 'prints']
[('upgraded', 0.8625801801681519)]
['2008', '年作', '美丽', '的', '悖论', '#', '

...

[('梳妆', 0.8821833729743958)]
['人物', '铝板', '画']
[('铝板', 0.9995927810668945)]
['1981', '年作', '天坛', '版画']
[('天坛', 0.9684370756149292)]
['2001', '年作', '黄河', '系列', '布上', '油彩']
[('布上', 0.9238803386688232)]
['丰收', '采橘', '布面', '油画']
[('采橘', 0.8444513082504272)]
['2012', '年作', '碧波', '泛舟', '纸本', '水粉', '、', '丙烯']
[('碧波', 0.7401250004768372)]
['2001', '年作', '无题', '（', '两幅', '）', '布面', '\u2003', '丙烯']
[('\u2003', 0.8457934260368347)]
['2011', '年作', '秋窗', '暗香', '庄周', '梦', '布面', '油画']
[('庄周', 0.755414605140686)]
['三个', '小男孩']
[('小男孩', 0.9902993440628052)]
['心荷', '布面', '油彩']
[('心荷', 0.9416559934616089)]
['1950', '—', '1960', '年代', '作', '芦雁', '纸本', '彩墨']
[('芦雁', 0.8388514518737793)]
['2006', '年作', '喝啤酒', '的', '女孩', '油彩', '布面']
[('喝啤酒', 0.9154276251792908)]
['1946', '年', '-', '1948', '年', '台湾', '生活', '组画', '木版']
[('组画', 0.7798874974250793)]
['金秋', '牛', '布面', '油彩']
[('金秋', 0.880510687828064)]
['西湖', '风景', '纸本', '油画']
[('西湖', 0.9588288068771362)]
['桌上', '的', '八角', '瓶花', '布面', '油画']
[('八角', 0.7583444118499

[('祖孙三代', 0.9954989552497864)]
['1966', '年作', '结构', '1966', '油彩', '画布']
[('1966', 0.9056581258773804)]
['2012', '年作', '入云龙', '油彩', '画布']
[('入云龙', 0.9073781967163086)]
['2007', '年作', '安全帽', '布面', '油画']
[('安全帽', 0.9889441728591919)]
['1976', '年作', '俯瞰', '的', '城市', '布面', '油画']
[('俯瞰', 0.9290115237236023)]
['西藏', '系列', '2', '—', '藏戏', '·', '格萨尔', '王传', '布面', '油画']
[('格萨尔', 0.8602877855300903)]
['1998', '年作', '快乐', '时光', 'NO.7', '布面', '油画']
[('NO.7', 0.9007537364959717)]
['1956', '年作', '风景', '纸本', '水彩']
[('水彩', 0.8002175688743591)]
['2002', '年作', '迹', '纸本', '版画']
[('迹', 0.9799827337265015)]
['2012', '年作', '老街', '正午', '水彩画']
[('正午', 0.8088180422782898)]
['养路', '木版']
[('养路', 0.8598660826683044)]
['桃花源', '水', '彩纸', '本', '镜框']
[('彩纸', 0.8507149815559387)]
['女孩', '布面', '油画']
[('女孩', 0.9634007215499878)]
['2004', '年作', '哈德逊', '河秋望', '布面', '油画']
[('布面', 0.7704730033874512)]
['1997', '年作', '透', '版画', 'E', '/', 'A']
[('E', 0.8025472164154053)]
['红叶', '溪流', '布面']
[('溪流', 0.8838070034980774)]
['冬景']
[

[('暖阳', 0.9671249389648438)]
['1992', '年作', '裸女', '与', '猫', '油画', '画布']
[('裸女', 0.8904954791069031)]
['听琴', '二女', '布面', '油画']
[('二女', 0.8268375396728516)]
['风景', '布上', '油画', '连框']
[('布上', 0.9097200632095337)]
['村落', '/', '乡村', '田野', '（', '两幅', '）', '油彩', '纸板']
[('纸板', 0.7568196654319763)]
['海港', '纸板', '油画']
[('海港', 0.8117661476135254)]
['2005', '年作', '山明水秀', '·', '徽州', '村落', '水彩', '法国', '康颂水', '彩纸']
[('康颂水', 0.7447078227996826)]
['放羊', '木版']
[('放羊', 0.9016323685646057)]
['湖光', '春色', '苍树', '鹿影', '（', '两件', '）', '银盐', '相纸']
[('湖光', 0.7592630386352539)]
['仕女', '与', '斑点', '骏马', '压克力', '彩纸', '本']
[('压克力', 0.7873239517211914)]
['风景', '框']
[('框', 0.9889222979545593)]
['1962', '年', '无标题', '油彩', '、', '画布']
[('无标题', 0.939350962638855)]
['向日葵']
[('向日葵', 1.0)]
['2008', '年作', '半亭', '风', '布面', '油彩']
[('半亭', 0.9221510887145996)]
['1986', '年作', '珍珠', '路', '—', '三峡', '夜航', '木刻', '套色', '纸本']
[('夜航', 0.7638444304466248)]
['1999', '年作', '鸡冠花', '油彩', '布面']
[('鸡冠花', 0.9644259214401245)]
['1993', '年作', '人体',

[('无题', 0.9316071271896362)]
['1982', '年作', '圭山', '写生', 'NO.11', '油彩', '木板']
[('NO.11', 0.814893364906311)]
['2007', '年作', '2007', '年', '第', '11r', '号', '油彩', '画布']
[('号', 0.9638670086860657)]
['女', '演奏家', '油彩', '画布']
[('演奏家', 0.9419354796409607)]
['Painted', 'in', '2009', 'Dream', 'of', 'Angel', 'I', 'oil', 'on', 'linen']
[('Allucaneet', 0.8479231595993042)]
['1982', '年作', '女子', '肖像', '油彩', '布面']
[('油彩', 0.7483342885971069)]
['滇池', '小景', '布面', '油画']
[('滇池', 0.9059938192367554)]
['2007', '年作', '肖像', '布面', '油画']
[('肖像', 0.8394824266433716)]
['2013', '年作', '霜', '冷', '长河', '布面', '油画']
[('长河', 0.7448618412017822)]
['风景', '人物', '油画', '画布']
[('画布', 0.9095245599746704)]
['2003', '年作', '硬石', '餐厅', '布上', '油画']
[('硬石', 0.8239326477050781)]
['2004', '年作', '你们', '能', '拥抱', '他', '吗', '？', '油画', '画布']
[('拥抱', 0.889121413230896)]
['肖像', '布面', '油画']
[('肖像', 0.9078589677810669)]
['浙西', '小景', '油彩', '画布']
[('浙西', 0.8805374503135681)]
['微风', '一牛', '石子', '与', '河', '（', '铜奖', '）', '油画', '画布']
[('一牛', 0.7125

[('组画', 0.8921458721160889)]
['2007', '年作', '无题', '布面', '油画']
[('无题', 0.964349091053009)]
['2008', '年作', '1', '！', '2', '！', '3', '！', '4', '！', '油彩', '丙烯', '画布']
[('丙烯', 0.9071553945541382)]
['1978', '年作', '矿山', '铁人', '布面', '油画']
[('铁人', 0.8258548378944397)]
['2003', '年作', '萨拉', '除去', '外罩', '11', '木', '画布', '框', '，', '乙稀']
[('外罩', 0.7230690717697144)]
['1960', '年代', '作', 'NINE', 'GOLDFISH', 'oil', 'on', 'masonite']
[('oil', 0.8097897171974182)]
['吃', '桃儿', '布面', '油画']
[('桃儿', 0.9457230567932129)]
['1999', '年作', '“', '异秀', '”', '人体', '油画', '系类', '之', '十二', '：', '“', '翠', '”']
[('”', 0.8509907126426697)]
['1990', '年', '1981', '年', '黄山', '晨曦', '翠雨', '江南', '木版']
[('翠雨', 0.8075044751167297)]
['1977', '年作', '台北', '孔庙', '水', '彩纸', '本']
[('彩纸', 0.8094006776809692)]
['1984', '年作', '青藏高原', '石板', '纸本']
[('青藏高原', 0.8461775183677673)]
['1998', '年作', '98', '日记', '·', '静物', '油画', '画布']
[('98', 0.7292649745941162)]
['乐在其中']
[('乐在其中', 1.0)]
['1985', '年作', '保罗', '与', '公牛', '油彩', '画布']
[('公牛', 0.8739511

In [26]:
artwork_sample.head()

id                                              title other_titles  \
0  1543491  1971年作 CORETAN RASA III （SCRIBBLES III） Acryli...          NaN   
1  1294000                                    2003年作 海礁 水彩  纸          NaN   
2  1308829                                         东北角渔村 油画画布          NaN   
3   809415                                      绿海深处有人家 水彩 纸本          NaN   
4  1256356                                               国师玄奘          NaN   

  artwork_category artwork_type display_price calc_price    year  technique  \
0               油画         西画雕塑           NaN        NaN  1971年作        NaN   
1             水粉水彩         西画雕塑           NaN        NaN  2003年作        NaN   
2               油画         西画雕塑           NaN        NaN      暂无        NaN   
3             水粉水彩         西画雕塑           NaN        NaN      暂无        NaN   
4               油画         西画雕塑           NaN        NaN      暂无        NaN   

   mounting  ...                                            image_url  \
0       NaN  ...    http://img2.artron.net/auction/2012/art501627/...   
1       NaN  ...    http://img2.artron.net/auction/old/art4223/d/a...   
2       NaN  ...    http://img3.artron.net/auction/2009/art8975/d/...   
3       NaN  ...    http://img4.artron.net/auction/2010/art9866/d/...   
4       NaN  ...    http://img1.artron.net/auction/old/art8014/d/a...   

   icon_img_url desc_origin                                  desc_origin_url  \
0           NaN         NaN  http://auction.artron.net/paimai-art5016270222/   
1           NaN         NaN    http://auction.artron.net/paimai-art42230751/   
2           NaN         NaN    http://auction.artron.net/paimai-art89750056/   
3           NaN         NaN    http://auction.artron.net/paimai-art98661822/   
4           NaN         NaN    http://auction.artron.net/paimai-art80140638/   

      info_update_time           created_at           updated_at  \
0  2015-07-12 15:48:29  2015-07-12 15:48:29  2015-07-12 15:48:29   
1  2015-07-12 04:33:45  2015-07-12 04:33:45  2015-07-12 04:33:45   
2  2015-07-12 05:03:47  2015-07-12 05:03:47  2015-07-12 05:03:47   
3  2015-07-10 14:29:20  2015-07-10 14:29:20  2015-07-10 14:29:20   
4  2015-07-12 03:15:50  2015-07-12 03:15:50  2015-07-12 03:15:50   

  comments_count likes_count vector  
0            0.0         0.0      0  
1            0.0         0.0      1  
2            0.0         0.0      2  
3            0.0         0.0      3  
4            0.0         0.0      4  

[5 rows x 23 columns]

In [11]:
model.similar_by_vector(title_vic, topn=1)


[('薄雪', 1.0)]

In [12]:
model.n_similarity(['玄奘', '法师'], ['玄奘', '佛教'])

0.85983458679852753

In [13]:
model.similarity('玄奘', '法师')

0.48091993682353268

In [14]:
model.similarity('玄奘', '佛教')

0.51991790420906192

In [15]:
frequency['油画']

290250

In [16]:
frequency['1923']

6805

In [17]:
frequency['90047']

0

In [30]:
artwork_vector


[array([ -1.93205715e-05,   1.21361269e-04,  -9.08907303e-05,
          1.20844814e-04,   2.20587741e-06,   1.03490933e-04,
          3.73605780e-05,  -2.26866751e-06,   1.26488762e-04,
         -4.68913263e-05,  -1.39109982e-04,  -1.57883572e-04,
          9.79407126e-05,   3.49093675e-05,   1.20331824e-05,
          6.99356305e-05,   4.87852797e-07,  -2.04636465e-04,
          1.38537430e-04,   5.92749986e-06,  -6.31428048e-06,
          2.44062502e-05,   1.21996415e-04,   7.80400424e-05,
          5.98574190e-05,   9.05833619e-06,   8.48577668e-05,
          2.95218938e-05,  -6.87437529e-05,   1.38061992e-04,
         -1.19871319e-04,   1.34285801e-05,   5.47011697e-05,
         -1.09450438e-04,  -1.58917744e-04,  -6.66722257e-05,
          1.82974436e-05,   5.85572826e-06,   3.86292045e-05,
         -1.54958940e-04,   9.76543024e-05,  -7.41355593e-05,
          1.00322640e-04,  -1.78890848e-05,  -3.31623611e-05,
          6.58212113e-05,  -9.56532125e-05,  -1.57231021e-04,
        